In [257]:
!pip install --upgrade cvxpy

Defaulting to user installation because normal site-packages is not writeable


In [258]:
!pip install botorch

Defaulting to user installation because normal site-packages is not writeable


In [259]:
import cvxpy as cp
import numpy as np
import matplotlib.pyplot as plt

from cvxpy import *
import pandas as pd
import seaborn as sns

import os
import torch

In [260]:
os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"


tkwargs = {
    "dtype": torch.double,
    #"device": torch.device("cuda" if torch.cuda.is_available() else "cpu"),
}
SMOKE_TEST = os.environ.get("SMOKE_TEST")

from __future__ import annotations

import math
from abc import ABC, abstractmethod
from math import pi
from typing import Optional

from botorch.test_functions.base import (
    ConstrainedBaseTestProblem,
    MultiObjectiveTestProblem,
)

In [279]:
#dataset macronutrients and micronutrients and others.

#Costs of raws
Costos=np.array([141.24,144.24,147.25,132.22,132.22,195.32,342.57,120.2,30.05,1803.03,111.18,336.56,152.65,150.25,159.27,136.73,300.5])
#CF
CF=np.array([4.5,2.8,2.5,24.7,6.1,5.6,1,8,0,0,22.5,0,17.8,14.5,5.7,2.3,0])
#Ca
Ca=np.array([0.06,0.04, 0.02, 1.75, 0.24,0.29,4.50,0.16,38.3,0.04, 0.35, 0, 0.98, 0.23, 0.10, 0.05, 32])
#AP
AP=np.array([0.13, 0.18, 0.05, 0.26, 0.03, 0.19, 2.45, 0.22, 0,0,0.17, 0, 0.04, 0.13, 0.15, 0.15,0])
#DM
DM=np.array([90.2,89.4, 86.3,91.2, 88.8, 88, 92, 88.6, 98, 98.5, 89.3, 0, 89.7, 90.8, 86.7, 89.4, 99.4])
#CP
CP=np.array([11.3, 11.6, 7.7, 16.7, 2.5, 44, 62.4, 19, 0, 95, 30.5, 0, 10.1,30.7, 21.5, 8.9, 0])
#Energy
Energy=np.array([14.7446, 15.4048, 14.9983,5.7664, 10.9456,15.3092,14.4188,12.5758,0,16.4095,9.9224,17.37,7.9859,  14.363 ,  14.4828,  15.2728, 0])
#L
L=np.array([0.4,0.33,0.22, 0.73, 0.09, 2.88, 4.75, 0.62, 0, 78, 1.06, 0, 0.59, 1.46, 1.55, 0.34, 0])
#MC
MC=np.array([0.43,0.46,0.33,0.45,0.06,1.28,2.36,0.83,0,0,1.25,0,0.22,0.66,0.56,0.37,0])
#T
T=np.array([0.37,0.34,0.27,0.7,0.07,1.75,2.65,0.74,0,0,1.06,0,0.47,0.99,0.82,0.3,0])
#Tp
Tp=np.array([0.13,0.13,0.06,0.31,0.02,0.59,0.65,0.13,0,0,0.43,0,0.1,0.25,0.19,0.1,0])



#Bounds of raws and macronutrients
supbd=10

bound=np.array([0.4, 0.4, 0.4, 0.05, 0.22, 1,0.04, 0.08,1,0.0065, 0.06, 0.04, 0.05, 0.1, 0.15, 0.2, 1])
Q=np.concatenate([CF, Ca, AP, DM, CP, MC, T, Tp, Energy, L]).reshape(10,17)
lower=np.array([0, 0.6, 0.15, 87, 18, 0.475, 0.627, 0.171, 14.001, 0.9501])
upper=np.array([6, supbd, supbd, 95, 21, supbd,supbd, supbd, 20,2])

#number of variables and standard deviation, and variances
n=17

ones=np.ones(n)

stdl = np.array([0.03962323, 0.0484768 , 0.01870829, 0.08031189, 0.02408319,0.13823892, 0.54625086, 0.09300538, 0., 0.,0.06356099, 0. , 0.08848729, 0.08757854, 0.06511528,0.03 , 0. ])
stde=np.array([0.3197, 0.4066, 0.2644, 1.0968, 0.5168, 0.3607, 1.4353, 0.5676,0.    , 0.    , 0.7056, 0.    , 1.4691, 0.5844, 0.3746, 0.2462,0.    ])

vare=np.diag(stde**2)
varl=np.diag(stdl**2)

In [280]:
def gensamples(nn):
    #rgn=np.random.seed(1234)
    lista=[]
    for i in range(nn):
        w=cp.Variable(n, pos=True)
        cons=cp.Constant(np.random.normal(160,2))
    

        objective_fct = cp.Maximize(1)


        constraints=[ones@w==1, Q@w>=lower, Q@w<=upper,
                     w[0]<=bound[0],
                     w[1]<=bound[1], 
                     w[2]<=bound[2],
                     w[3]<=bound[3],
                     w[4]<=bound[4], 
                     w[5]<=bound[5],
                     w[6]<=bound[6],
                     w[7]<=bound[7],
                     w[8]<=bound[8],
                     w[9]<=bound[9], 
                     w[10]<=bound[10],
                     w[11]<=bound[11],
                     w[12]<=bound[12], 
                     w[13]<=bound[13],
                     w[14]<=bound[14],
                     w[15]<=bound[15],
                     w[16]<=bound[16],
                     Costos@w.T-cons<=0]
        prob = cp.Problem(objective_fct, constraints)
        assert  prob.is_dqcp()
        prob.solve(qcp=True, solver='ECOS')
        #xvalue=w.value/t.value
        lista.append(w.value)
    return np.array(lista)

In [281]:
Costos=torch.as_tensor(Costos).to(**tkwargs)

CF=torch.as_tensor(CF).to(**tkwargs)
Ca=torch.as_tensor(Ca).to(**tkwargs)
AP=torch.as_tensor(AP).to(**tkwargs)
DM=torch.as_tensor(DM).to(**tkwargs)
CP=torch.as_tensor(CP).to(**tkwargs)
MC=torch.as_tensor(MC).to(**tkwargs)
Tp=torch.as_tensor(Tp).to(**tkwargs)
T=torch.as_tensor(T).to(**tkwargs)
L=torch.as_tensor(L).to(**tkwargs)
Energy=torch.as_tensor(Energy).to(**tkwargs)
ones=torch.as_tensor(ones).to(**tkwargs)

stdl =torch.as_tensor(stdl).to(**tkwargs)
stde=torch.as_tensor(stde).to(**tkwargs)


vare=torch.diag(stde**2)
varl=torch.diag(stdl**2)


In [282]:
class myfunction(MultiObjectiveTestProblem):

    
    dim = 17
    num_objectives=3

    lower=torch.zeros(17)
    upper=torch.as_tensor(bound)
 
    _bounds=torch.stack([lower, upper])
   
    _ref_point=[-170,0,0]
    
    
    def __init__(self, noise_std: Optional[float] = None, negate: bool = False) -> None:
        r"""
        Args:
            noise_std: Standard deviation of the observation noise.
            negate: If True, negate the objectives.
        """
        super().__init__(noise_std=noise_std, negate=negate)

    def _f1(self, X:Tensor)-> Tensor:
          
        return -Costos@torch.transpose(X,1,0)

    def _f2(self, X:Tensor)-> Tensor:
           
        return  L@torch.transpose(X,1,0)
    
    def  _f3(self, X:Tensor)-> Tensor:
       
        return Energy@torch.transpose(X,1,0)
    
    def evaluate_true(self, X: Tensor) -> Tensor:
        F1 = self._f1(X=X)
        F2 = self._f2(X=X)
        F3 = self._f3(X=X)
        return torch.stack([F1,F2,F3],dim=-1)

In [283]:
problem=myfunction().to(**tkwargs)

/home/in2lab/.local/lib/python3.10/site-packages/botorch/test_functions/base.py:39: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  "bounds", torch.tensor(self._bounds, dtype=torch.float).transpose(-1, -2)


In [284]:
from botorch.models.gp_regression import FixedNoiseGP
from botorch.models.model_list_gp_regression import ModelListGP
from botorch.models.transforms.outcome import Standardize
from gpytorch.mlls.sum_marginal_log_likelihood import SumMarginalLogLikelihood
from botorch.utils.transforms import unnormalize, normalize
from botorch.utils.sampling import draw_sobol_samples

NOISE_SE = torch.tensor([0.1,0.1,0.1], **tkwargs)

def generate_initial_data(n):
    # generate training data
    train_x = torch.tensor(gensamples(n)).to(**tkwargs)
    train_obj_true = problem(train_x)
    train_obj = train_obj_true + torch.randn_like(train_obj_true) * NOISE_SE
    
    return train_x, train_obj

def initialize_model(train_x, train_obj):
    # define models for objective and constraint
    train_x = normalize(train_x, problem._bounds)
    models = []
    for i in range(train_obj.shape[-1]):
        train_y = train_obj[..., i:i+1]
        train_yvar = torch.full_like(train_y, NOISE_SE[i] ** 2)
        models.append(
            FixedNoiseGP(train_x, train_y, train_yvar, outcome_transform=Standardize(m=1))
        )
    model = ModelListGP(*models)
    mll = SumMarginalLogLikelihood(model.likelihood, model)
    return mll, model

In [285]:
from botorch import fit_gpytorch_model
from botorch.sampling import SobolQMCNormalSampler
from botorch.exceptions import BadInitialCandidatesWarning
from botorch.utils.multi_objective.pareto import is_non_dominated
from botorch.utils.multi_objective.box_decompositions.non_dominated import FastNondominatedPartitioning

import time
import warnings

In [286]:
ineqconstr=[(torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -CF, -6),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), Ca, 0.6),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -Ca, -supbd),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), AP, 0.15),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -AP, -supbd),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), DM, 87),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -DM, -95),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), CP, 18),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -CP, -21),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), MC, 0.475),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), Tp, 0.171),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), T, 0.627),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -MC, -supbd),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -Tp, -supbd),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -T, -supbd),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), Energy, 14.001),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -Energy, -20),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), L, 0.9501),
            (torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), -L, -2),
            
           ]
eqconstr=[(torch.tensor([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16]), ones, 1),]

In [287]:
from botorch.acquisition.objective import GenericMCObjective, IdentityMCObjective
from botorch.utils.multi_objective.scalarization import get_chebyshev_scalarization
from botorch.acquisition.multi_objective.monte_carlo import qExpectedHypervolumeImprovement, qNoisyExpectedHypervolumeImprovement
from botorch.optim.optimize import optimize_acqf, optimize_acqf_list

In [288]:
def optimize_qehvi_and_get_observation(model, train_x, train_obj, sampler):
    """Optimizes the qEHVI acquisition function, and returns a new candidate and observation."""
    # partition non-dominated space into disjoint rectangles
    with torch.no_grad():
        pred = model.posterior(normalize(train_x, problem._bounds)).mean
        partitioning = FastNondominatedPartitioning(
        ref_point=problem.ref_point, 
        Y=pred,
    )
    acq_func = qExpectedHypervolumeImprovement(
        model=model,
        ref_point=problem.ref_point.tolist(),
        partitioning=partitioning,
        #X_baseline=normalize(train_x, problem._bounds),
        #inequality_constraints=ineqconstr,
        #equality_constraints=eqconstr,
        sampler=sampler,
        
    )
    # optimize
    candidates, _ = optimize_acqf(
        acq_function=acq_func,
        bounds=problem._bounds,
        q=1,
        num_restarts=10,
        raw_samples=256,
        #batch_initial_conditions=train_x.reshape(b,1,17),
        inequality_constraints=ineqconstr,
        equality_constraints=eqconstr,
        options={"batch_limit": 5, "maxiter": 200},
        sequential=True,
    )
        
    # observe new values 
    new_x =  candidates
    new_obj = problem(new_x)
    #new_obj = new_obj_true + torch.randn_like(new_obj_true) * NOISE_SE
    return new_x, new_obj, #new_obj_true

In [289]:
import pickle

In [290]:


# Guardar los resultados en un archivo utilizando pickle
with open('resultados.pkl', 'wb') as archivo:
    pickle.dump(resultados, archivo)


NameError: name 'resultados' is not defined

In [ ]:
Values=[10*i for i in range(1,13)]
EXP1=[]
for value in Values:
    EXP=[]
    print(f'value={value}')
    
    seeds = np.random.randint(0, 1000,30)
    print(seeds)

    for i in range(30):
        N_BATCH = 50 if not SMOKE_TEST else 10
        MC_SAMPLES = 256 if not SMOKE_TEST else 16

        verbose = True

        seed=int(seeds[i])
        print(f"Seed: {seed}")   
        np.random.seed(seed)
        torch.manual_seed(seed)
       
        

        hvs_ehvi=[]
        nume=[]

        # call helper functions to generate initial training data and initialize model
        train_x_ehvi, train_obj_ehvi = generate_initial_data(n=value)
        #train_x_ehvi=train_x_ehvi1 
        #train_obj_ehvi=train_obj_ehvi1
        mll_ehvi, model_ehvi = initialize_model(train_x_ehvi, train_obj_ehvi)


        # compute hypervolume
        bd = FastNondominatedPartitioning(ref_point=problem.ref_point, Y=train_obj_ehvi)
        volume = bd.compute_hypervolume().item()
        nume.append(bd.pareto_Y.shape[0])


        hvs_ehvi.append(volume)

        # run N_BATCH rounds of BayesOpt after the initial random batch
        for iteration in range(1, N_BATCH + 1):    

            t0 = time.monotonic()

            # fit the models

            fit_gpytorch_model(mll_ehvi)


            # define the qEI and qNEI acquisition modules using a QMC sampler

            ehvi_sampler = SobolQMCNormalSampler(MC_SAMPLES, seed=seed)


            # optimize acquisition functions and get new observations

            new_x_ehvi, new_obj_ehvi= optimize_qehvi_and_get_observation(
                model_ehvi,train_x_ehvi, train_obj_ehvi, ehvi_sampler
            )


            train_x_ehvi = torch.cat([train_x_ehvi, new_x_ehvi])
            train_obj_ehvi = torch.cat([train_obj_ehvi, new_obj_ehvi])





            #compute hypervolume
            bd = FastNondominatedPartitioning(ref_point=problem.ref_point, Y=train_obj_ehvi)
            volume = bd.compute_hypervolume().item()
            hvs_ehvi.append(volume)
            nume.append(bd.pareto_Y.shape[0])




            mll_ehvi, model_ehvi = initialize_model(train_x_ehvi, train_obj_ehvi)


            t1 = time.monotonic()
            EXP.append([value,seed, volume, bd.pareto_Y.shape[0],bd.pareto_Y, train_x_ehvi, train_obj_ehvi])
        
            if verbose:
                print(
                     f"\nBatch {iteration:>2}:", 
                     f"Hypervolume (qEHVI) = {hvs_ehvi[-1]:>4.4f}", 
                     f"#Paprox={bd.pareto_Y.shape[0]}",   
                     f"time = {t1-t0:>4.2f}", 
                     f"Lysine= {(new_x_ehvi[-1]@L.T).item():>4.4f}",
                     f"Energy= {(new_x_ehvi[-1]@Energy).item():>4.4f}",
                     f"Costs= {(new_x_ehvi[-1]@Costos.T).item():>4.4f}", end=")")
            else:
                print(".", end="")
            
    
        lista = globals()[f'EXP']
        filename = f'EXP_{value}.pickle'
        with open(filename, 'wb') as file:
            pickle.dump(lista, file)

 

value=10
[ 46 139 297 257 488 635 957  40 377 910 812 839 799 469  89 772 723 578
 757 472 711 399  80 774 184 373 461 509 850 369]
Seed: 46

Batch  1: Hypervolume (qEHVI) = 345.0177 #Paprox=7 time = 2.07 Lysine= 0.9501 Energy= 14.4152 Costs= 150.5449)
Batch  2: Hypervolume (qEHVI) = 345.0177 #Paprox=7 time = 2.06 Lysine= 1.2651 Energy= 14.0517 Costs= 167.5158)
Batch  3: Hypervolume (qEHVI) = 357.5680 #Paprox=8 time = 2.13 Lysine= 0.9501 Energy= 14.4071 Costs= 149.6281)
Batch  4: Hypervolume (qEHVI) = 358.4153 #Paprox=9 time = 2.29 Lysine= 0.9501 Energy= 14.4614 Costs= 150.6914)
Batch  5: Hypervolume (qEHVI) = 372.9439 #Paprox=10 time = 2.50 Lysine= 0.9501 Energy= 14.4666 Costs= 148.5822)
Batch  6: Hypervolume (qEHVI) = 372.9439 #Paprox=11 time = 2.34 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9329)
Batch  7: Hypervolume (qEHVI) = 372.9439 #Paprox=12 time = 2.47 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9330)
Batch  8: Hypervolume (qEHVI) = 372.9439 #Paprox=12 time = 2.51 Lysine= 0.9501

Batch 22: Hypervolume (qEHVI) = 413.4434 #Paprox=24 time = 3.75 Lysine= 0.9501 Energy= 14.4715 Costs= 146.5670)
Batch 23: Hypervolume (qEHVI) = 413.4434 #Paprox=25 time = 2.22 Lysine= 0.9501 Energy= 14.4715 Costs= 146.5670)
Batch 24: Hypervolume (qEHVI) = 413.4434 #Paprox=26 time = 3.67 Lysine= 0.9501 Energy= 14.4715 Costs= 146.5670)
Batch 25: Hypervolume (qEHVI) = 413.4434 #Paprox=27 time = 2.53 Lysine= 0.9501 Energy= 14.4715 Costs= 146.5670)
Batch 26: Hypervolume (qEHVI) = 413.4434 #Paprox=28 time = 3.11 Lysine= 0.9501 Energy= 14.4715 Costs= 146.5670)
Batch 27: Hypervolume (qEHVI) = 413.4434 #Paprox=28 time = 4.28 Lysine= 0.9501 Energy= 14.4715 Costs= 146.5670)
Batch 28: Hypervolume (qEHVI) = 413.4434 #Paprox=29 time = 3.48 Lysine= 0.9501 Energy= 14.4715 Costs= 146.5670)
Batch 29: Hypervolume (qEHVI) = 413.4434 #Paprox=29 time = 4.95 Lysine= 0.9501 Energy= 14.4715 Costs= 146.5670)
Batch 30: Hypervolume (qEHVI) = 413.4434 #Paprox=29 time = 4.44 Lysine= 0.9501 Energy= 14.4715 Costs= 14

Batch 45: Hypervolume (qEHVI) = 353.1795 #Paprox=44 time = 2.19 Lysine= 0.9501 Energy= 14.5057 Costs= 151.6075)
Batch 46: Hypervolume (qEHVI) = 353.1795 #Paprox=45 time = 2.34 Lysine= 0.9501 Energy= 14.5057 Costs= 151.6075)
Batch 47: Hypervolume (qEHVI) = 353.1795 #Paprox=46 time = 2.23 Lysine= 0.9501 Energy= 14.5057 Costs= 151.6075)
Batch 48: Hypervolume (qEHVI) = 353.1795 #Paprox=46 time = 2.56 Lysine= 0.9501 Energy= 14.5057 Costs= 151.6075)
Batch 49: Hypervolume (qEHVI) = 353.1795 #Paprox=47 time = 2.42 Lysine= 0.9501 Energy= 14.5057 Costs= 151.6075)
Batch 50: Hypervolume (qEHVI) = 353.1795 #Paprox=48 time = 2.34 Lysine= 0.9501 Energy= 14.5057 Costs= 151.6075)Seed: 257

Batch  1: Hypervolume (qEHVI) = 421.1077 #Paprox=8 time = 2.48 Lysine= 0.9501 Energy= 14.4048 Costs= 145.8333)
Batch  2: Hypervolume (qEHVI) = 421.1077 #Paprox=8 time = 2.07 Lysine= 1.2295 Energy= 14.0010 Costs= 161.8330)
Batch  3: Hypervolume (qEHVI) = 442.3238 #Paprox=9 time = 1.88 Lysine= 0.9501 Energy= 14.1151 Co

Batch 18: Hypervolume (qEHVI) = 440.9539 #Paprox=25 time = 3.81 Lysine= 1.2033 Energy= 14.0010 Costs= 155.7469)
Batch 19: Hypervolume (qEHVI) = 440.9539 #Paprox=25 time = 3.16 Lysine= 1.2033 Energy= 14.0010 Costs= 155.7469)
Batch 20: Hypervolume (qEHVI) = 440.9539 #Paprox=26 time = 3.62 Lysine= 1.2033 Energy= 14.0010 Costs= 155.7469)
Batch 21: Hypervolume (qEHVI) = 440.9539 #Paprox=27 time = 5.67 Lysine= 1.2033 Energy= 14.0010 Costs= 155.7469)
Batch 22: Hypervolume (qEHVI) = 440.9539 #Paprox=28 time = 5.55 Lysine= 1.2033 Energy= 14.0010 Costs= 155.7469)
Batch 23: Hypervolume (qEHVI) = 440.9539 #Paprox=28 time = 5.91 Lysine= 1.2033 Energy= 14.0010 Costs= 155.7469)
Batch 24: Hypervolume (qEHVI) = 440.9539 #Paprox=29 time = 4.86 Lysine= 1.2033 Energy= 14.0010 Costs= 155.7469)
Batch 25: Hypervolume (qEHVI) = 440.9539 #Paprox=30 time = 3.97 Lysine= 1.2033 Energy= 14.0010 Costs= 155.7469)
Batch 26: Hypervolume (qEHVI) = 440.9539 #Paprox=30 time = 4.29 Lysine= 1.2033 Energy= 14.0010 Costs= 15

Batch 41: Hypervolume (qEHVI) = 440.8346 #Paprox=38 time = 2.35 Lysine= 1.2341 Energy= 14.0403 Costs= 154.7042)
Batch 42: Hypervolume (qEHVI) = 440.8346 #Paprox=38 time = 3.59 Lysine= 1.2341 Energy= 14.0403 Costs= 154.7042)
Batch 43: Hypervolume (qEHVI) = 440.8346 #Paprox=38 time = 2.52 Lysine= 1.2341 Energy= 14.0403 Costs= 154.7042)
Batch 44: Hypervolume (qEHVI) = 440.8346 #Paprox=39 time = 2.60 Lysine= 1.2341 Energy= 14.0403 Costs= 154.7042)
Batch 45: Hypervolume (qEHVI) = 440.8346 #Paprox=40 time = 2.57 Lysine= 1.2341 Energy= 14.0403 Costs= 154.7042)
Batch 46: Hypervolume (qEHVI) = 440.8346 #Paprox=41 time = 2.78 Lysine= 1.2341 Energy= 14.0403 Costs= 154.7042)
Batch 47: Hypervolume (qEHVI) = 440.8346 #Paprox=42 time = 2.42 Lysine= 1.2341 Energy= 14.0403 Costs= 154.7042)
Batch 48: Hypervolume (qEHVI) = 440.8346 #Paprox=43 time = 2.47 Lysine= 1.2341 Energy= 14.0403 Costs= 154.7042)
Batch 49: Hypervolume (qEHVI) = 440.8346 #Paprox=44 time = 2.50 Lysine= 1.2341 Energy= 14.0403 Costs= 15

Batch 14: Hypervolume (qEHVI) = 423.1806 #Paprox=20 time = 2.16 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9329)
Batch 15: Hypervolume (qEHVI) = 423.1806 #Paprox=21 time = 2.37 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9329)
Batch 16: Hypervolume (qEHVI) = 423.1806 #Paprox=22 time = 2.25 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9329)
Batch 17: Hypervolume (qEHVI) = 423.1806 #Paprox=23 time = 2.12 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9329)
Batch 18: Hypervolume (qEHVI) = 423.1806 #Paprox=24 time = 2.08 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9329)
Batch 19: Hypervolume (qEHVI) = 423.1806 #Paprox=25 time = 2.21 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9329)
Batch 20: Hypervolume (qEHVI) = 423.1806 #Paprox=26 time = 2.16 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9329)
Batch 21: Hypervolume (qEHVI) = 423.1806 #Paprox=27 time = 2.30 Lysine= 0.9501 Energy= 14.4608 Costs= 150.9329)
Batch 22: Hypervolume (qEHVI) = 423.1806 #Paprox=28 time = 2.95 Lysine= 0.9501 Energy= 14.4608 Costs= 15

In [236]:
def optimize_qNehvi_and_get_observation(model, train_x, train_obj, sampler):
    """Optimizes the qEHVI acquisition function, and returns a new candidate and observation."""
    # partition non-dominated space into disjoint rectangles
    with torch.no_grad():
        pred = model.posterior(normalize(train_x, problem._bounds)).mean
        partitioning = FastNondominatedPartitioning(
        ref_point=problem.ref_point, 
        Y=pred,
    )
    acq_func = qNoisyExpectedHypervolumeImprovement(
        model=model,
        ref_point=problem.ref_point.tolist(),
        partitioning=partitioning,
        X_baseline=normalize(train_x, problem._bounds),
        #inequality_constraints=ineqconstr,
        #equality_constraints=eqconstr,
        sampler=sampler,
        
    )
    # optimize
    candidates, _ = optimize_acqf(
        acq_function=acq_func,
        bounds=problem._bounds,
        q=1,
        num_restarts=10,
        raw_samples=256,
        #batch_initial_conditions=train_x.reshape(b,1,17),
        inequality_constraints=ineqconstr,
        equality_constraints=eqconstr,
        options={"batch_limit": 5, "maxiter": 200},
        sequential=True,
    )
        
    # observe new values 
    new_x =  candidates
    new_obj = problem(new_x)
    #new_obj = new_obj_true + torch.randn_like(new_obj_true) * NOISE_SE
    return new_x, new_obj, #new_obj_true

In [237]:
Values=[10*i for i in range(2,13)]
EXP1=[]
for value in Values:
    EXP=[]
    print(f'value={value}')
    
    seeds = np.random.randint(0, 1000,30)
    print(seeds)

    for i in range(30):
        N_BATCH = 50 if not SMOKE_TEST else 10
        MC_SAMPLES = 256 if not SMOKE_TEST else 16

        verbose = True

        #seed=92
       
        seed=int(seeds[i])
        print(f"Seed: {seed}")   
        np.random.seed(seed)
        torch.manual_seed(seed)

        hvs_ehvi=[]
        nume=[]

        # call helper functions to generate initial training data and initialize model
        train_x_ehvi, train_obj_ehvi = generate_initial_data(n=value)
        #train_x_ehvi=train_x_ehvi1 
        #train_obj_ehvi=train_obj_ehvi1
        mll_ehvi, model_ehvi = initialize_model(train_x_ehvi, train_obj_ehvi)


        # compute hypervolume
        bd = FastNondominatedPartitioning(ref_point=problem.ref_point, Y=train_obj_ehvi)
        volume = bd.compute_hypervolume().item()
        nume.append(bd.pareto_Y.shape[0])


        hvs_ehvi.append(volume)

        # run N_BATCH rounds of BayesOpt after the initial random batch
        for iteration in range(1, N_BATCH + 1):    

            t0 = time.monotonic()

            # fit the models

            fit_gpytorch_model(mll_ehvi)


            # define the qEI and qNEI acquisition modules using a QMC sampler

            ehvi_sampler = SobolQMCNormalSampler(MC_SAMPLES, seed=seed)


            # optimize acquisition functions and get new observations

            new_x_ehvi, new_obj_ehvi= optimize_qNehvi_and_get_observation(
                model_ehvi,train_x_ehvi, train_obj_ehvi, ehvi_sampler
            )


            train_x_ehvi = torch.cat([train_x_ehvi, new_x_ehvi])
            train_obj_ehvi = torch.cat([train_obj_ehvi, new_obj_ehvi])





            #compute hypervolume
            bd = FastNondominatedPartitioning(ref_point=problem.ref_point, Y=train_obj_ehvi)
            volume = bd.compute_hypervolume().item()
            hvs_ehvi.append(volume)
            nume.append(bd.pareto_Y.shape[0])




            mll_ehvi, model_ehvi = initialize_model(train_x_ehvi, train_obj_ehvi)


            t1 = time.monotonic()
            EXP.append([value,seed, volume, bd.pareto_Y.shape[0],bd.pareto_Y, train_x_ehvi, train_obj_ehvi])
        
            if verbose:
                print(
                     f"\nBatch {iteration:>2}:", 
                     f"Hypervolume (qEHVI) = {hvs_ehvi[-1]:>4.4f}", 
                     f"#Paprox={bd.pareto_Y.shape[0]}",   
                     f"time = {t1-t0:>4.2f}", 
                     f"Lysine= {(new_x_ehvi[-1]@L.T).item():>4.4f}",
                     f"Energy= {(new_x_ehvi[-1]@Energy).item():>4.4f}",
                     f"Costs= {(new_x_ehvi[-1]@Costos.T).item():>4.4f}", end=")")
            else:
                print(".", end="")
            
    
        lista = globals()[f'EXP']
        filename = f'EXP_{value}N.pickle'
        with open(filename, 'wb') as file:
            pickle.dump(lista, file)

 

value=20
[656 475 438 771 984 631 759 562 663 360 713 849  53  98 465 713 895 294
 120 757 644 149 291 209 996 131 136 225 950 206]
Seed: 656

Batch  1: Hypervolume (qEHVI) = 411.4398 #Paprox=12 time = 9.98 Lysine= 0.9501 Energy= 14.3879 Costs= 146.2891)
Batch  2: Hypervolume (qEHVI) = 411.4398 #Paprox=12 time = 9.93 Lysine= 1.2651 Energy= 14.0517 Costs= 167.5158)
Batch  3: Hypervolume (qEHVI) = 413.3024 #Paprox=13 time = 10.16 Lysine= 0.9501 Energy= 14.4715 Costs= 146.5670)
Batch  4: Hypervolume (qEHVI) = 440.6304 #Paprox=14 time = 10.86 Lysine= 0.9501 Energy= 14.1151 Costs= 144.2513)
Batch  5: Hypervolume (qEHVI) = 460.5382 #Paprox=15 time = 11.20 Lysine= 1.1511 Energy= 14.0010 Costs= 149.3117)
Batch  6: Hypervolume (qEHVI) = 463.1895 #Paprox=16 time = 11.14 Lysine= 1.1403 Energy= 14.5443 Costs= 152.5799)
Batch  7: Hypervolume (qEHVI) = 463.1895 #Paprox=17 time = 10.47 Lysine= 1.1403 Energy= 14.5443 Costs= 152.5799)
Batch  8: Hypervolume (qEHVI) = 463.1895 #Paprox=18 time = 11.31 Lys

/home/in2lab/.local/lib/python3.10/site-packages/linear_operator/utils/cholesky.py:40: NumericalWarning: A not p.d., added jitter of 1.0e-08 to the diagonal
  warnings.warn(



Batch  9: Hypervolume (qEHVI) = 463.1895 #Paprox=19 time = 11.45 Lysine= 1.1403 Energy= 14.5443 Costs= 152.5799)

/home/in2lab/.local/lib/python3.10/site-packages/linear_operator/utils/cholesky.py:40: NumericalWarning: A not p.d., added jitter of 1.0e-08 to the diagonal
  warnings.warn(



Batch 10: Hypervolume (qEHVI) = 463.1895 #Paprox=20 time = 11.92 Lysine= 1.1403 Energy= 14.5443 Costs= 152.5799)

...


Batch 49: Hypervolume (qEHVI) = 453.7211 #Paprox=80 time = 40.22 Lysine= 0.9501 Energy= 14.1151 Costs= 144.2513)

/home/in2lab/.local/lib/python3.10/site-packages/linear_operator/utils/cholesky.py:40: NumericalWarning: A not p.d., added jitter of 1.0e-08 to the diagonal
  warnings.warn(



Batch 50: Hypervolume (qEHVI) = 453.7211 #Paprox=81 time = 42.36 Lysine= 0.9501 Energy= 14.1151 Costs= 144.2513)Seed: 446


/home/in2lab/.local/lib/python3.10/site-packages/linear_operator/utils/cholesky.py:40: NumericalWarning: A not p.d., added jitter of 1.0e-08 to the diagonal
  warnings.warn(


KeyboardInterrupt: 